In [1]:
import nltk
from nltk.stem import WordNetLemmatizer
import torch
from torch import nn
import matplotlib.pyplot as plt
from matplotlib import ticker
import time
import math
import numpy as np
import random
from helpers import load_data, process_intents, bag_of_words
import fitz
import re
import json
import pandas as pd

In [2]:
intents_dict, response_dict = load_data('../raw_data/intents.json')
n_categories = len(intents_dict)
print(n_categories)

14


# Programmatically expand intents sections, starting with greeting

In [3]:
# load the data
pdf_path = "../raw_data/thesaurus.pdf"
doc = fitz.open(pdf_path)
text = ""
for page in doc:
    text += page.get_text("text")

print(text)

HIGH PRAISE FOR
ROGET’S 21st CENTURY THESAURUS
in Dictionary Form
“Exceptional . . . unique words and groupings . . .
this source is a gem!”
—Booklist
“OUTSTANDING!”
—American Bookseller
“INNOVATIVE . . .  CLEAN, THOROUGH . . . a word that 
can be almost tasted is accessed in nanoseconds. 
It’s close to instant gratiﬁcation, and 
a perfect adjunct to the dictionary . . . 
This thesaurus ﬁts the meaning of the word. 
IT’S A TREASURE.”
—San Diego Writers’ Monthly
“A SOLID FRAME OF REFERENCE.”
—USA Today
TOMORROW’S CLASSIC FOR TODAY’S USER
QUANTITY SALES
Most Dell books are available at special quantity discounts when
purchased in bulk by corporations, organizations, or groups. Special
imprints, messages, and excerpts can be produced to meet your needs.
For more information, write to: Dell Publishing, 1745 Broadway,
New York, NY 10019. Attention: Director, Special Markets.
INDIVIDUAL SALES
Are there any Dell books you want but cannot ﬁnd in your local
stores? If so, you can order them dir

Dont need intro text

In [4]:
trimmed_text = text[text.find("aback"):]
print(trimmed_text[:1000])

aback [adv] taken unawares confused, surprised,
thrown off, thrown off guard*; concept 403
abaft [adj] to the rear astern, back, behind,
rearward; concepts 586,820
abandon [n] careless disregard for conse-
quences disregard, freedom, impulse, 
licentiousness, recklessness, spontaneity,
thoughtlessness, uninhibitedness, unrestraint,
wantonness, wildness; concepts 633,645
—Ant. restraint, self-restraint
abandon [v1] leave behind, relinquish abdicate,
back out, bail out*, bow out*, chicken out*, cop
out*, cut loose*, desert, discard, discontinue,
ditch*, drop, drop out, duck*, dump*, dust*,
ﬂake out*, ﬂy the coop*, give up the ship*, kiss
goodbye*, leave, leg it*, let go, opt out, pull out,
quit, run out on, screw*, ship out, stop, storm
out*, surrender, take a powder*, take a walk*,
throw over*, vacate, walk out on, wash hands
of*, withdraw, yield; concept 195 —Ant.
cherish, defend, keep, pursue, retain, support
abandon [v2] leave in troubled state back out,
desert, disown, forsake, jilt

In [5]:
# Regex pattern to match the word, the middle part including square brackets, and the definition
start_pattern = r"(\w+)\s\[\w+\d?\]\s(.+)"
end_pattern = r";? ?concepts? \d{1,3}"
lines = trimmed_text.split("\n")
start_text = ""
text_cleaned = []

for i in range(len(lines)):
    start_match = re.match(start_pattern, lines[i])
    if start_match:
        word, start_text = start_match.groups()

        for j in range(i+1, len(lines)):
            end_match = re.search(end_pattern, lines[j])
            if end_match:
                start_text += re.split(end_pattern, lines[j])[0]
                i = j
                break
            else:
                start_text += lines[j]

        text_cleaned.append((word, start_text))

In [6]:
# look for word in the text
def find_syns(word_to_find, context):
    syns = []
    for word, definition in text_cleaned:
        if word == word_to_find and context in definition:
            possible_responses = definition.split(",")
            for response in possible_responses:
                syns.append(response.strip())

    return syns

# gets all occurences of the word "good". Not every "good" works for our context, so we add some (context, that is).
# For now, i'll just manually edit it.
print(find_syns("good", "excellent"))

['pleasant', 'ﬁne acceptable', 'ace*', 'admirable', 'agreeable', 'bad', 'boss*', 'bully', 'capital', 'choice', 'commendable', 'congenial', 'crack*', 'deluxe', 'excellent', 'exceptional', 'favorable', 'ﬁrst-class', 'ﬁrst-rate', 'gnarly*', 'gratifying', 'great', 'honorable', 'marvelous', 'neat*', 'nice', 'pleasing', 'positive', 'precious', 'prime', 'rad*', 'recherché*', 'reputable', 'satisfactory', 'satisfying', 'select', 'ship-shape*', 'sound', 'spanking*', 'splendid', 'sterling', 'stupendous', 'super', 'superb', 'super-eminent', 'super-excellent', 'superior', 'tip-top*', 'up to snuff*', 'valuable', 'welcome', 'wonderful', 'worthy;']


# adding greeting intents

Get rid of synonyms that don't make sense for our purposes. Copied from above and manually edited

In [7]:
good_greeting_syns = ['excellent', 'great', 'marvelous', 'nice', 'splendid', 'wonderful', 'amazing']
greetings = ["Hello", "Hi", "Hey", "Greetings"]
responses = ["Well hello", "Hello", "Hi", "Salutations"]
greeting_extra = ["How are you?", "How's it going?", "Hope you're well."]
response_extra = ["I'm doing well, thank you.", "It's going.", "I am well, thank you for asking."]
extras = ["as well", "too", "also"]

def a_or_an(word):
    if word == "excellent" or word == "amazing":
        return "an " + word
    else:
        return "a " + word 


for syn in good_greeting_syns:
    greetings.append(f"{syn.capitalize()} to see you")
    responses.append(f"{syn.capitalize()} to see you {random.choice(extras)}")
    greeting_extra.append(f"Hope you're having {a_or_an(syn)} day.")
    response_extra.append(f"Thanks, I am having {a_or_an(syn)} day")

greetings.append("Howdy")
responses.append("Howdy partner")
greeting_extra.append("")
response_extra.append("")

In [8]:
# Ensure greetings and responses have the same length
# as they're used to map between each other
thanks = ["thanks", "thank you", "thank you very much", "thanks a lot", "thank you so much", "thanks so much", "thank you kindly", "thank you for that."]
times_of_day = ["morning", "afternoon", "evening"]
initial_inquiry = ["How may I assist you today?", "What can I do for you today?", "How can I help you today?", "What brings you here today?", "How may I be of service?",
                   "How can I be of assistance?", "What can I do for you?", "What brings you here?", "How can I help you?", "What can I do for you today?", "How may I assist you?"]

# Function to generate greetings
def generate_greetings(number_of_greetings=10):
    generated_greetings = []
    generated_responses = []
    
    for _ in range(number_of_greetings):
        # Select a random index
        index = random.randint(0, len(greetings) - 1)
        # Use random index to keep track of corresponding response
        greeting = greetings[index]
        response = responses[index]
        time_of_day = random.choice(times_of_day + [""])  # Add an option for no specific time of day
        index_extra = random.randint(0, len(greeting_extra) - 1)
        extra_g = greeting_extra[index_extra]
        extra_r = response_extra[index_extra]
        middle_g = ""
        middle_r = ""
        inquiry = random.choice(initial_inquiry)

        # layers and layers of variation for the dataset
        # if time_of_day chosen from times and not empty string
        if time_of_day:
            choice_of_three = random.choice(extras)
            middle_g = f" and good {time_of_day}."
            middle_r = f", and good {time_of_day} to you {choice_of_three}."
        else:
            middle_g = ""
            middle_r = ""
        
        # Construct the greeting and response
        full_greeting = f"{greeting}{middle_g} {extra_g}"
        full_response = f"{response}{middle_r} {extra_r} {inquiry}"
        
        # Add the greeting and response to the lists
        generated_greetings.append(full_greeting.strip())
        generated_responses.append(full_response.strip())
    
    return generated_greetings, generated_responses

# Generate and print 20 different greetings and responses
greetings, responses = generate_greetings(20)
for i in range(len(greetings)):
    print("Input: " + greetings[i])
    print("Response: " + responses[i])

Input: Splendid to see you and good morning. Hope you're having a nice day.
Response: Splendid to see you as well, and good morning to you too. Thanks, I am having a nice day How may I be of service?
Input: Wonderful to see you Hope you're having a marvelous day.
Response: Wonderful to see you also Thanks, I am having a marvelous day How may I assist you?
Input: Marvelous to see you and good evening. Hope you're having an excellent day.
Response: Marvelous to see you as well, and good evening to you too. Thanks, I am having an excellent day What can I do for you today?
Input: Greetings and good morning. How's it going?
Response: Salutations, and good morning to you too. It's going. What can I do for you today?
Input: Greetings Hope you're having an amazing day.
Response: Salutations Thanks, I am having an amazing day How may I assist you today?
Input: Marvelous to see you and good evening. Hope you're having a marvelous day.
Response: Marvelous to see you as well, and good evening to y

Save updated intents

In [9]:
intents_dict['greeting'] = greetings
response_dict['greeting'] = responses

# adding goodbye intents

In [10]:
print(intents_dict['goodbye'])

['Bye', 'See you later', 'Goodbye', 'Nice chatting to you, bye', 'Till next time']


In [11]:
find_syns("goodbye", "farewell")

['farewell statement adieu',
 'adios',
 'bye-bye',
 'cheerio',
 'ciao',
 'godspeed*',
 'leave-tak-ing',
 'parting',
 'so long*',
 'swan song*',
 'toodle-oo*;']

In [12]:
goodbye_syns = find_syns("goodbye", "farewell")
goodbye_syns.remove("leave-tak-ing")
goodbye_syns.remove("godspeed*") # debated on keeping this
goodbye_syns.remove("swan song*")
goodbye_syns.remove("toodle-oo*;")
goodbye_syns.remove("parting")
print(goodbye_syns)

['farewell statement adieu', 'adios', 'bye-bye', 'cheerio', 'ciao', 'so long*']


In [13]:
goodbye_syns[0] = goodbye_syns[0].split(" ")[0] # remove the extra words from the first one
# remove '*' from the end of the words
goodbye_syns = [word.strip("*") for word in goodbye_syns]
print(goodbye_syns)

['farewell', 'adios', 'bye-bye', 'cheerio', 'ciao', 'so long']


In [14]:
goodbye_templates = []
response_templates = []
goodbye_syns.append("goodbye")
goodbye_syns.append("till next time")
goodbye_syns.append("see you later")
goodbye_syns.append("bye")
welcome_phrases = ["You're welcome", "No problem", "No worries", "It's my pleasure", "Don't mention it", "My pleasure", "Anytime", "You're very welcome", "No need to thank me", "It was my pleasure", "I'm glad to be of service"]
for syn in goodbye_syns:
    goodbye_templates.append(f"{syn.capitalize()}! Thanks for your help.")
    goodbye_templates.append(f"{syn.capitalize()}! Have {a_or_an(random.choice(good_greeting_syns))} day.") # using these from the greeting sec
    goodbye_templates.append(f"{syn.capitalize()}! Take care.")
    goodbye_templates.append(f"{syn.capitalize()}! Thanks again.")
    goodbye_templates.append(f"{syn.capitalize()}! Thanks for helping.")
    goodbye_templates.append(f"{syn.capitalize()}! Have a good one.")
    goodbye_templates.append(f"{syn.capitalize()}! You've been a great help.")
    goodbye_templates.append(f"{syn.capitalize()}!")
    response_templates.append(f"{random.choice(welcome_phrases)}. Take care.")
    response_templates.append(f"You {random.choice(extras)}. Please come again.")
    response_templates.append(f"You {random.choice(extras)}. Have {a_or_an(random.choice(good_greeting_syns))} day.")
    response_templates.append(f"{random.choice(welcome_phrases)}. Have {a_or_an(random.choice(good_greeting_syns))} day.")
    response_templates.append(f"{random.choice(welcome_phrases)}, it's what I'm here for. Take care.")
    response_templates.append("And you as well. Please come again.")
    response_templates.append(f"{random.choice(welcome_phrases)}. Have {a_or_an(random.choice(good_greeting_syns))} day.")
    response_templates.append(f"Have {a_or_an(random.choice(good_greeting_syns))} day.")

print(goodbye_templates)
print(response_templates)

['Farewell! Thanks for your help.', 'Farewell! Have a wonderful day.', 'Farewell! Take care.', 'Farewell! Thanks again.', 'Farewell! Thanks for helping.', 'Farewell! Have a good one.', "Farewell! You've been a great help.", 'Farewell!', 'Adios! Thanks for your help.', 'Adios! Have a marvelous day.', 'Adios! Take care.', 'Adios! Thanks again.', 'Adios! Thanks for helping.', 'Adios! Have a good one.', "Adios! You've been a great help.", 'Adios!', 'Bye-bye! Thanks for your help.', 'Bye-bye! Have a nice day.', 'Bye-bye! Take care.', 'Bye-bye! Thanks again.', 'Bye-bye! Thanks for helping.', 'Bye-bye! Have a good one.', "Bye-bye! You've been a great help.", 'Bye-bye!', 'Cheerio! Thanks for your help.', 'Cheerio! Have a nice day.', 'Cheerio! Take care.', 'Cheerio! Thanks again.', 'Cheerio! Thanks for helping.', 'Cheerio! Have a good one.', "Cheerio! You've been a great help.", 'Cheerio!', 'Ciao! Thanks for your help.', 'Ciao! Have a marvelous day.', 'Ciao! Take care.', 'Ciao! Thanks again.', 

In [15]:
intents_dict['goodbye'] = goodbye_templates
response_dict['goodbye'] = response_templates

# Adding thanks intents

In [16]:
print(intents_dict['thanks'])

['Thanks', 'Thank you', "That's helpful", 'Awesome, thanks', 'Thanks for helping me']


In [17]:
print(response_dict['thanks'])

['Happy to help!', 'Any time!', 'My pleasure']


In [18]:
thanks = thanks + intents_dict['thanks']
responses = welcome_phrases + response_dict['thanks']
print(thanks)
print(responses)

['thanks', 'thank you', 'thank you very much', 'thanks a lot', 'thank you so much', 'thanks so much', 'thank you kindly', 'thank you for that.', 'Thanks', 'Thank you', "That's helpful", 'Awesome, thanks', 'Thanks for helping me']
["You're welcome", 'No problem', 'No worries', "It's my pleasure", "Don't mention it", 'My pleasure', 'Anytime', "You're very welcome", 'No need to thank me', 'It was my pleasure', "I'm glad to be of service", 'Happy to help!', 'Any time!', 'My pleasure']


In [19]:
first_part = ['Thank you very much.', 'Thanks a lot.', 'Thank you so much.', 'Thanks so much.', 'Thank you kindly.', 'Thank you for that.', 'Thanks.', 'Thank you.', "That's helpful, thanks.", 'Awesome, thanks.', 'Thanks for helping me.', "I appreciate it."]
second_part_nouns = ["lifesaver", "star", "gem", "legend", "hero", "saint", "miracle worker", "godsend", "savior", "treasure"]
second_part = [" You've been a great help.", " You're a great help", " I don't know what I'd do without you."]

for noun in second_part_nouns:
    second_part.append(f" You're a {noun}.")
    second_part.append("") # for variation

In [20]:
# drop first two elements of thanks, they're redundant
thanks = thanks[2:]
# capitalize the first letter of each element
thanks = [word.capitalize() for word in thanks]
print(thanks)
print(responses)

['Thank you very much', 'Thanks a lot', 'Thank you so much', 'Thanks so much', 'Thank you kindly', 'Thank you for that.', 'Thanks', 'Thank you', "That's helpful", 'Awesome, thanks', 'Thanks for helping me']
["You're welcome", 'No problem', 'No worries', "It's my pleasure", "Don't mention it", 'My pleasure', 'Anytime', "You're very welcome", 'No need to thank me', 'It was my pleasure', "I'm glad to be of service", 'Happy to help!', 'Any time!', 'My pleasure']


In [21]:
# remove '!' at the end of each element of responses
responses = [word.strip("!") for word in responses]
print(responses)

["You're welcome", 'No problem', 'No worries', "It's my pleasure", "Don't mention it", 'My pleasure', 'Anytime', "You're very welcome", 'No need to thank me', 'It was my pleasure', "I'm glad to be of service", 'Happy to help', 'Any time', 'My pleasure']


In [22]:
anything_else = ['Do you need anything else?',
                 'How can I assist you further?',
                 'Is there anything else I can help with?', 
                 'What else can I do for you?', 'What else do you need?', 
                 'How else can I help you?', 
                 'Is there anything else I can do for you?', 
                 'What else can I do for you today?']

thanks = []
res = []

for i in range(100):
    full_thanks = random.choice(first_part) + random.choice(second_part)
    full_response = random.choice(responses) + ". " + random.choice(anything_else)
    thanks.append(full_thanks)
    res.append(full_response)

intents_dict['thanks'] = thanks
response_dict['thanks'] = res

# Remove noanswer, as I believe it serves no purpose

In [23]:
intents_dict.pop('noanswer')
response_dict.pop('noanswer')

["Sorry, can't understand you",
 'Please give me more info',
 'Not sure I understand']

# adding options intents

In [24]:
print(intents_dict['options'])

['How you could help me?', 'What you can do?', 'What help you provide?', 'How you can be helpful?', 'What support is offered']


In [25]:
print(response_dict['options'])

['I can guide you through Adverse drug reaction list, Blood pressure tracking, Hospitals and Pharmacies', 'Offering support for Adverse drug reaction, Blood pressure, Hospitals and Pharmacies']


# Todo: make responses more varied (?)

In [26]:
def generate_options(number_of_options=10):
    options = []
    responses = []
    end_part = ["?", " here?", " today?", " right now?", " now?", " this evening?", " this morning?", " this afternoon?"]
    help = ["help", "assist", "support"]
    choices = ["options", "choices"]
    response_options = ['I can guide you through the adverse drug reaction list, blood pressure tracking, or find hospitals and pharmacies.',
                        'I can offer you support by giving you information on the adverse drug reaction list, blood pressure tracking, or finding hospitals and pharmacies.',
                        'I can help you with the adverse drug reaction list, blood pressure tracking, or finding hospitals and pharmacies.']


    for i in range(number_of_options):
        options.append(f"What are my {random.choice(choices)}{random.choice(end_part)}")
        options.append(f"What can I do{random.choice(end_part)}")
        options.append(f"What can you {random.choice(help)} me with{random.choice(end_part)}")
        options.append(f"How can you {random.choice(help)} me{random.choice(end_part)}")
        options.append(f"What can you do for me{random.choice(end_part)}")

    return options, response_options

options, responses = generate_options(20)

Save the updated options

In [27]:
intents_dict['options'] = options
response_dict['options'] = responses

# adding adverse_drug intents

In [28]:
intents_dict['adverse_drug']

['How to check Adverse drug reaction?',
 'Open adverse drugs module',
 'Give me a list of drugs causing adverse behavior',
 'List all drugs suitable for patient with adverse reaction',
 'Which drugs dont have adverse reaction?']

In [29]:
response_dict['adverse_drug']

['Navigating to Adverse drug reaction module']

In [30]:
def generate_adverse_drug_question(number_of_questions=10):
    inquiries = []
    # data collected using code in named_entity_recognition.ipynb
    medications = pd.read_csv('../clean_data/medications.csv')
    choices = ['bad', 'adverse']
    interactions = ['interactions', 'effects', 'side effects', 'behavior']
    display = ['display', 'show', 'list', 'provide', 'give']
    med_syns = ['medications', 'drugs', 'pharmaceuticals', 'prescriptions', 'meds', 'medicines']
    time = ['at the same time?', 'simultaneously?', 'together?']

    for i in range(number_of_questions):
        inquiries.append(f"Give me a list of {random.choice(med_syns)} causing {random.choice(choices)} {random.choice(interactions)}")
        inquiries.append(f"Which {random.choice(med_syns)} have {random.choice(choices)} {random.choice(interactions)}?")
        inquiries.append(f"{random.choice(display).capitalize()} all {random.choice(med_syns)} with {random.choice(choices)} {random.choice(interactions)}")
        inquiries.append(f"Is it safe to take {random.choice(medications['medication'].values)} and {random.choice(medications['medication'].values)} {random.choice(time)}")
        inquiries.append(f"Do {random.choice(medications['medication'].values)} and {random.choice(medications['medication'].values)} have {random.choice(choices)} {random.choice(interactions)}?")

    return inquiries

inquiries = generate_adverse_drug_question(20)
intents_dict['adverse_drug'] = inquiries

# adding blood-pressure intents

In [31]:
intents_dict['blood_pressure']

['Open blood pressure module',
 'Task related to blood pressure',
 'Blood pressure data entry',
 'I want to log blood pressure results',
 'Blood pressure data management']

In [32]:
response_dict['blood_pressure']

['Navigating to Blood Pressure module']

In [33]:
def generate_blood_pressure_question(number_of_questions=10):
    inquiries = []
    data = ['results', 'data', 'information', 'readings', 'numbers', 'stats']
    open_module = ['Open', 'Show', 'Display', 'Start', 'Run', 'Begin', 'Launch']
    module = ['module', 'management']
    log = ['log', 'record', 'track']
    for i in range(number_of_questions):
        inquiries.append(f"{random.choice(open_module)} the {random.choice(module)} for blood pressure")
        inquiries.append(f"{random.choice(open_module)} blood pressure {random.choice(data)}")
        inquiries.append(f"{random.choice(open_module)} blood pressure {random.choice(module)}")
        inquiries.append(f"I want to {random.choice(log)} my blood pressure {random.choice(data)}")
        inquiries.append(f"Blood pressure {random.choice(data)} {random.choice(module)}")

    return inquiries

inquiries = generate_blood_pressure_question(20)
intents_dict['blood_pressure'] = inquiries

# adding blood_pressure_search intents

In [34]:
intents_dict['blood_pressure_search']

['I want to search for blood pressure result history',
 'Blood pressure for patient',
 'Load patient blood pressure result',
 'Show blood pressure results for patient',
 'Find blood pressure results by ID']

In [35]:
def generate_blood_pressure_search(number_of_searches=10):
    searches = []
    search = ['search for', 'find', 'locate', 'view', 'show', 'display', 'pull up', 'load']
    result = ['results', 'data', 'information', 'readings', 'numbers', 'stats', 'history', 'logs', 'records']
    for i in range(number_of_searches):
        searches.append(f"I want to {random.choice(search)} blood pressure {random.choice(result)}")
        searches.append(f"{random.choice(search).capitalize()} blood pressure {random.choice(result)}")
        searches.append(f"{random.choice(search).capitalize()} blood pressure {random.choice(result)} for patient.")
        searches.append(f"{random.choice(search).capitalize()} blood pressure {random.choice(result)} by ID.")
    
    searches.append("Blood pressure for patient")

    return searches

searches = generate_blood_pressure_search(20)
intents_dict['blood_pressure_search'] = searches

# adding search_blood_pressure_by_patient_id intents

In [36]:
intents_dict['search_blood_pressure_by_patient_id']

[]

In [37]:
def generate_random_patient_ids(num_ids=10, prefix="P", id_length=6):
    random_ids = []
    for _ in range(num_ids):
        id_number = ''.join([str(random.randint(0, 9)) for _ in range(id_length)])
        random_ids.append(prefix + id_number)
    return random_ids

# Generate 10 random patient IDs
random_patient_ids = generate_random_patient_ids()

for id in random_patient_ids:
    print(id)

P641525
P438284
P362468
P754015
P817415
P813956
P327412
P680548
P168553
P758495


In [38]:
def generate_search_by_patient_id(num_searches=10):
    searches = []
    search = ['search for', 'find', 'locate', 'view', 'show', 'display', 'pull up', 'load']
    result = ['results', 'data', 'information', 'readings', 'numbers', 'stats', 'history', 'logs', 'records']
    for i in range(num_searches):
        searches.append(f"I want to {random.choice(search)} blood pressure {random.choice(result)} for patient {random.choice(random_patient_ids)}")
        searches.append(f"{random.choice(search).capitalize()} blood pressure {random.choice(result)} for patient {random.choice(random_patient_ids)}")
        searches.append(f"{random.choice(random_patient_ids)} blood pressure {random.choice(result)}")
        searches.append(random.choice(random_patient_ids))
    
    return searches

searches = generate_search_by_patient_id(20)
intents_dict['search_blood_pressure_by_patient_id'] = searches

# adding pharmacy_search intents

In [39]:
intents_dict['pharmacy_search']

['Find me a pharmacy',
 'Find pharmacy',
 'List of pharmacies nearby',
 'Locate pharmacy',
 'Search pharmacy']

In [40]:
def generate_pharmacy_search(num_searches=10):
    searches = []
    search = ['search for', 'find', 'locate', 'show', 'navigate to']
    location = ['location', 'address', 'home', 'position']
    pharmacy = ['pharmacy', 'drugstore', 'pharmacies', 'drugstores']
    for i in range(num_searches):
        searches.append(f"I want to {random.choice(search)} a pharmacy")
        searches.append(f"{random.choice(search).capitalize()} a pharmacy")
        searches.append(f"{random.choice(search).capitalize()} {random.choice(pharmacy)}")
        searches.append(f"{random.choice(search).capitalize()} {random.choice(pharmacy)} near me")
        searches.append(f"{random.choice(search).capitalize()} {random.choice(pharmacy)} near my {random.choice(location)}")
        searches.append(f"{random.choice(search).capitalize()} nearyby {random.choice(pharmacy)}")

    
    return searches

searches = generate_pharmacy_search(20)
intents_dict['pharmacy_search'] = searches

# adding hospital_search intents

In [41]:
intents_dict['hospital_search']

['Lookup for hospital',
 'Searching for hospital to transfer patient',
 'I want to search hospital data',
 'Hospital lookup for patient',
 'Looking up hospital details']

In [42]:
def generate_hospital_search(num_searches=10):
    searches = []
    search = ['search for', 'find', 'locate', 'view', 'show', 'display', 'pull up', 'load', 'lookup']
    hospital = ['hospital', 'hospitals']
    location = ['location', 'address', 'home', 'position']


    for i in range(num_searches):
        searches.append(f"I want to {random.choice(search)} a hospital")
        searches.append(f"{random.choice(search).capitalize()} a hospital")
        searches.append(f"{random.choice(search).capitalize()} {random.choice(hospital)}")
        searches.append(f"{random.choice(search).capitalize()} {random.choice(hospital)} near me")
        searches.append(f"{random.choice(search).capitalize()} {random.choice(hospital)} near my {random.choice(location)}")
        searches.append(f"{random.choice(search).capitalize()} nearyby {random.choice(hospital)}")
    
    return searches

searches = generate_hospital_search(20)
intents_dict['hospital_search'] = searches

In [43]:
# Load the original JSON file
with open('../raw_data/intents.json', 'r') as file:
    data = json.load(file)

# Update the JSON structure with new patterns and responses
for intent in data["intents"]:
    tag = intent["tag"]
    if tag in intents_dict:
        intent["patterns"] = intents_dict[tag]
    if tag in response_dict:
        intent["responses"] = response_dict[tag]

# Write the updated JSON structure back to a file
with open('../clean_data/intents_enriched.json', 'w') as file:
    json.dump(data, file, indent=4)